In [8]:
import os
import requests
import json
import time
from dotenv import load_dotenv

load_dotenv()

# 이러한 환경 변수를 설정하거나 다음 값을 편집해야 합니다.
endpoint = os.getenv("EXER_AZURE_OPENAI_ENDPOINT")  
deployment = "sora"
subscription_key = os.getenv("AZURE_T2V_API_KEY")

api_version = "preview"
path = f'openai/v1/video/generations/jobs'
params = f'?api-version={api_version}'
constructed_url = endpoint + path + params

headers = {
  'Api-Key': subscription_key,
  'Content-Type': 'application/json',
}

body = {
  "prompt": "항공기가 날아다니는 들판의 풍경",
  "n_variants": "1",
  "n_seconds": "5",
  "height": "480",
  "width": "854",
  "model": deployment,
}

job_response = requests.post(constructed_url, headers=headers, json=body)
if not job_response.ok:
    print("❌ Video generation failed.")
    print(json.dumps(job_response.json(), sort_keys=True, indent=4, separators=(',', ': ')))
else:
    print(json.dumps(job_response.json(), sort_keys=True, indent=4, separators=(',', ': ')))
    job_response = job_response.json()
    job_id = job_response.get("id")
    status = job_response.get("status")
    status_url = f"{endpoint}openai/v1/video/generations/jobs/{job_id}?api-version={api_version}"

    print(f"⏳ Polling job status for ID: {job_id}")
    while status not in ["succeeded", "failed"]:
        time.sleep(5)
        job_response = requests.get(status_url, headers=headers).json()
        status = job_response.get("status")
        print(f"Status: {status}")

    if status == "succeeded":
        generations = job_response.get("generations", [])
        if generations:
            print(f"✅ Video generation succeeded.")

            generation_id = generations[0].get("id")
            video_url = f'{endpoint}openai/v1/video/generations/{generation_id}/content/video{params}'
            video_response = requests.get(video_url, headers=headers)
            if video_response.ok:
                output_filename = "output.mp4"
                with open(output_filename, "wb") as file:
                    file.write(video_response.content)
                print(f'Generated video saved as "{output_filename}"')
        else:
            print("⚠️ Status is succeeded, but no generations were returned.")
    elif status == "failed":
        print("❌ Video generation failed.")
        print(json.dumps(job_response, sort_keys=True, indent=4, separators=(',', ': ')))

{
    "created_at": 1764213855,
    "expires_at": null,
    "failure_reason": null,
    "finished_at": null,
    "generations": [],
    "height": 480,
    "id": "task_01kb1ne5e8e0fsgvywf519cea5",
    "inpaint_items": null,
    "model": "sora",
    "n_seconds": 5,
    "n_variants": 1,
    "object": "video.generation.job",
    "prompt": "\ud56d\uacf5\uae30\uac00 \ub0a0\uc544\ub2e4\ub2c8\ub294 \ub4e4\ud310\uc758 \ud48d\uacbd",
    "status": "preprocessing",
    "width": 854
}
⏳ Polling job status for ID: task_01kb1ne5e8e0fsgvywf519cea5
Status: preprocessing
Status: running
Status: processing
Status: processing
Status: succeeded
✅ Video generation succeeded.
Generated video saved as "output.mp4"


In [9]:
from IPython.display import Video

Video("output.mp4", embed=True, width=640, height=480)